In [1]:
import assemblyai as aai

In [2]:
aai.settings.api_key = "3bc5ca9c34754d5baa7dae38b6041003"
transcript = aai.Transcriber().transcribe(r"C:\Users\PC\Test_Emile_Agri\What_is_agriculture_other_.mp4")
subtitles = transcript.export_subtitles_srt()
f = open(r"C:\Users\PC\Test_Emile_Agri\subtitles.srt", "a")
f.write(subtitles)
f.close()

In [3]:
import torch
from mmtafrica.mmtafrica import load_params, translate
from huggingface_hub import hf_hub_download

In [4]:
# Define language map and model parameters
language_map = {'English': 'en', 'Fon': 'fon'}
checkpoint = hf_hub_download(repo_id="chrisjay/mmtafrica", filename="mmt_translation.pt")
device = 'cuda' if torch.cuda.is_available() else 'cpu'
params = load_params({'checkpoint': checkpoint, 'device': device})

def get_translation(source_language, target_language, source_sentence):
    '''
    Function to get translation using the mmtafrica model.
    '''
    source_lang = language_map[source_language]
    target_lang = language_map[target_language]
    return translate(params, source_sentence, source_lang=source_lang, target_lang=target_lang)

def process_srt_file(input_file_path, output_file_path):
    '''
    Process and translate an SRT file from English to Fon.
    '''
    with open(input_file_path, 'r', encoding='utf-8') as file:
        lines = file.readlines()

    with open(output_file_path, 'w', encoding='utf-8') as out_file:
        buffer = []
        for line in lines:
            if line.strip().isdigit():
                if buffer:
                    translated_text = get_translation('English', 'Fon', ' '.join(buffer))
                    out_file.write(f"{index}{timeframe}{translated_text}\n\n")
                    buffer = []
                index = line
            elif '-->' in line:
                timeframe = line
            elif line.strip() == '':
                continue
            else:
                buffer.append(line.strip())

        # Translate and write the last buffered subtitle if any
        if buffer:
            translated_text = get_translation('English', 'Fon', ' '.join(buffer))
            out_file.write(f"{index}\n{timeframe}\n{translated_text}\n\n")

# Path to your SRT file and the output file
input_srt_path = r"C:\Users\PC\Test_Emile_Agri\subtitles.srt"
output_srt_path = r"C:\Users\PC\Test_Emile_IA\subtitles_fon.srt"
process_srt_file(input_srt_path, output_srt_path)

C:\Users\PC\AppData\Roaming\Python\Python39\site-packages\torch\_tensor.py:575: UserWarning: floor_divide is deprecated, and will be removed in a future version of pytorch. It currently rounds toward 0 (like the 'trunc' function NOT 'floor'). This results in incorrect rounding for negative values.
To keep the current behavior, use torch.div(a, b, rounding_mode='trunc'), or for actual floor division, use torch.div(a, b, rounding_mode='floor'). (Triggered internally at  ..\aten\src\ATen\native\BinaryOps.cpp:467.)
  return torch.floor_divide(self, other)


  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

...

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

In [9]:
# # Place files in this path or modify the paths to point to where the files are
# srtfilename = r"C:\Users\PC\Supertranslate.ai-main_orig\Supertranslate.ai-main\Burn_Subtitles_Into_Video\AI_SaaS.srt"
# mp4filename = r"C:\Users\PC\Supertranslate.ai-main_orig\Supertranslate.ai-main\Burn_Subtitles_Into_Video\AI_SaaS.mp4"
srtfilename = r"C:\Users\PC\Test_Emile_IA\subtitles_fon.srt"
mp4filename = r"C:\Users\PC\Test_Emile_Agri\What_is_agriculture_other_.mp4"

import sys
import pysrt
from moviepy.editor import VideoFileClip, TextClip, CompositeVideoClip

def time_to_seconds(time_obj):
    return time_obj.hours * 3600 + time_obj.minutes * 60 + time_obj.seconds + time_obj.milliseconds / 1000


def create_subtitle_clips(subtitles, videosize,fontsize=24, font='Ubuntu', color='white', debug = False):
    subtitle_clips = []

    for subtitle in subtitles:
        start_time = time_to_seconds(subtitle.start)
        end_time = time_to_seconds(subtitle.end)
        duration = end_time - start_time

        video_width, video_height = videosize
        
        text_clip = TextClip(subtitle.text, fontsize=fontsize, font=font, color=color, bg_color = 'black',size=(video_width*3/4, None), method='caption').set_start(start_time).set_duration(duration)
        subtitle_x_position = 'center'
        subtitle_y_position = video_height* 4 / 5 

        text_position = (subtitle_x_position, subtitle_y_position)                    
        subtitle_clips.append(text_clip.set_position(text_position))

    return subtitle_clips



In [10]:
import os
os.environ["IMAGEMAGICK_BINARY"] = r"C:\Program Files\ImageMagick-7.0.10-Q16\magick.exe"  # Adjust the path as needed

from moviepy.editor import VideoFileClip, CompositeVideoClip, TextClip
import pysrt

# Load video and SRT file
video = VideoFileClip(mp4filename)
subtitles = pysrt.open(srtfilename)

begin,end= mp4filename.split(".mp4")
output_video_file = begin+'_subtitled'+".mp4"

print ("Output file name: ",output_video_file)

# Create subtitle clips
subtitle_clips = create_subtitle_clips(subtitles,video.size)

# Add subtitles to the video
final_video = CompositeVideoClip([video] + subtitle_clips)

# Write output video file
final_video.write_videofile(output_video_file)


Output file name:  C:\Users\PC\Test_Emile_Agri\What_is_agriculture_other__subtitled.mp4
Moviepy - Building video C:\Users\PC\Test_Emile_Agri\What_is_agriculture_other__subtitled.mp4.
MoviePy - Writing audio in What_is_agriculture_other__subtitledTEMP_MPY_wvf_snd.mp3


MoviePy - Done.
Moviepy - Writing video C:\Users\PC\Test_Emile_Agri\What_is_agriculture_other__subtitled.mp4



Moviepy - Done !
Moviepy - video ready C:\Users\PC\Test_Emile_Agri\What_is_agriculture_other__subtitled.mp4


In [11]:
from IPython.display import HTML
from base64 import b64encode
mp4 = open(output_video_file,'rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
HTML("""
<video width=400 controls>
      <source src="%s" type="video/mp4">
</video>
""" % data_url)